In [1]:
import pandas as pd 
import numpy as np 
import re 
from nltk.corpus import stopwords 
from nltk.tokenize import TweetTokenizer 
from nltk.stem.wordnet import WordNetLemmatizer 
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, TfidfTransformer 
from sklearn.linear_model import LogisticRegression 
from sklearn.svm import SVC 
from sklearn.svm import LinearSVC 
from sklearn.calibration import CalibratedClassifierCV 
from sklearn.metrics import roc_auc_score 
from scipy.sparse import csr_matrix, hstack 
import lightgbm as lgb

In [2]:
PATH = '../data/'

train = pd.read_csv(PATH + 'cleaned_train.csv')
test = pd.read_csv(PATH + 'cleaned_test.csv')


train_sentence = train['comment_text_cleaned_polarity']
test_sentence = test['comment_text_cleaned_polarity']


train_sentence_retain_punctuation = train['comment_text_cleaned_retain_punctuation']
test_sentence_retain_punctuation = test['comment_text_cleaned_retain_punctuation']

text = train_sentence

text_retain_punctuation = train_sentence_retain_punctuation


print(train.shape)
print(test.shape)

(159571, 30)
(153164, 24)


In [3]:


phrase_vectorizer = TfidfVectorizer(ngram_range=(1,3),
                                    strip_accents='unicode', 
                                    max_features=100000, 
                                    analyzer='word',
                                    sublinear_tf=True,
                                    token_pattern=r'\w{1,}')
char_vectorizer = TfidfVectorizer(ngram_range=(2,5), 
                                  strip_accents='unicode', 
                                  max_features=200000, 
                                  analyzer='char', 
                                  sublinear_tf=True)

print('fitting char')
char_vectorizer.fit(text_retain_punctuation.values)
print('fitting phrase')
phrase_vectorizer.fit(text.values)

print('transforming train skip gram')

print('transforming train char')
train_char = char_vectorizer.transform(train_sentence_retain_punctuation.values)
print('transforming train phrase')
train_phrase = phrase_vectorizer.transform(train_sentence.values)


print('transforming test char')
test_char = char_vectorizer.transform(test_sentence_retain_punctuation.values)
print('transforming test phrase')
test_phrase = phrase_vectorizer.transform(test_sentence.values)


train_tfidf = hstack((train_char, train_phrase), format='csr')
test_tfidf = hstack((test_char, test_phrase), format='csr')

label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']

train_tfidf

fitting char
fitting phrase
transforming train skip gram
transforming train char
transforming train phrase
transforming test char
transforming test phrase


<159571x300000 sparse matrix of type '<class 'numpy.float64'>'
	with 162813546 stored elements in Compressed Sparse Row format>

In [24]:
# from sklearn.model_selection import train_test_split
# x_train, x_val, y_train_df, y_val_df = train_test_split(train_tfidf, train, test_size=0.33)
# # Split the dataset



# Split the dataset
split_index = round(len(train) * 0.8) #################################
# shuffled_train = train#.sample(frac=1)
x_train = train_tfidf[:split_index]
y_train_df = train.iloc[:split_index]
#######
x_val = train_tfidf[split_index:]
y_val_df = train.iloc[split_index:]
# Get test data ready
x_test = test_tfidf


# train toxic
def pr(y_i, y, train_features):
    p = train_features[y==y_i].sum(0)
    return (p + 1) / ((y == y_i).sum() + 1)
r_dict = {label: np.log(pr(1, y_train_df[label].values, x_train) / pr(0,  y_train_df[label].values, x_train)) for label in label_cols}

In [25]:
train_set = {label: x_train.multiply(r_dict[label]).tocsr() for label in r_dict }
val_set = {label: x_val.multiply(r_dict[label]).tocsr() for label in r_dict }
test_set = {label: x_test.multiply(r_dict[label]).tocsr() for label in r_dict }

# del r_dict, x_train, x_val
import gc
gc.collect()


2015

In [ ]:
del r_dict, x_train, x_val
import gc
gc.collect()

0

In [ ]:
for 
lgb_train_set = lgb.Dataset(train_set['toxic'], y_train_df['toxic'].values)
lgb_eval_set = lgb.Dataset(val_set['toxic'], y_val_df['toxic'].values, reference=lgb_train_set)


# params = {
#     'task': 'train',
#     'boosting_type': 'gbdt',
#     'objective': 'binary',
#     'metric': {'binary', 'auc'},
#     'learning_rate': 0.2,
#     'num_iterations': 100,
#     'num_leaves': 171,
#     'device': 'cpu',
#     'num_threads': 24,
#     'max_depth': -1,
# #     'min_data_in_leaf': 5,
#     'bagging_fraction': 0.8,
#     'bagging_freq': 1,
#     'feature_fraction': 0.8,
#     'lambda_l1': 1,
#     'lambda_l2': 1}


params = {
    'learning_rate': 0.2,
    'application': 'binary',
    'num_leaves': 31,
    'verbosity': -1,
    'metric': 'auc',
    'data_random_seed': 2,
    'bagging_fraction': 0.8,
    'feature_fraction': 0.6,
    'nthread': 4,
    'lambda_l1': 1,
    'lambda_l2': 1
} 

gbm = lgb.train(params,
                lgb_train_set,
                valid_sets=lgb_eval_set,
               verbose_eval=10)



In [ ]:
from sklearn.metrics import roc_auc_score
y = y_val_df['toxic']
pred = gbm.predict(val_set['toxic'])
print('accuracy is {}'.format(roc_auc_score(y,pred)))

In [ ]:
inv_char = {v: k for k, v in char_vectorizer.vocabulary_.items()}
inv_phrase = {v: k for k, v in phrase_vectorizer.vocabulary_.items()}
features = []
features_char = [inv_char[i] for i in range(0,train_char.shape[1] )]
features_phrase = [inv_phrase[i] for i in range(0,train_phrase.shape[1])]
features.extend(features_char)
features.extend(features_phrase)

In [ ]:
df_importance = pd.DataFrame()
df_importance['score'] = pd.Series(gbm.feature_importance()) 
df_importance['feature'] = pd.Series(features)

In [ ]:
df_importance.sort_values(by=['score'], ascending=False)

In [74]:
cols = {'combination_id': [], 'learning_rate':[], 'num_leaves':[], 
        'bagging_fraction':[], 'feature_fraction':[], 'lambda_l1':[], 
        'lambda_l2':[], 'label':[],'roc':[],'trained':[], 'max_depth': [], 
        'num_iterations': [], 'tp': [], 'fp': [], 'precision': []}
df_lgb = pd.DataFrame(cols)
learning_rate = [ 0.2, 0.1, 0.05]
num_leaves = [11,31, 61,]
max_depth = [3,4,5]
bag_frt = [0.9, 0.8,0.7]
feature_fraction = [1, 0.8,0.6]
lambda_l1 = [1, 0, 0.5]
lambda_l2 = [1, 0, 0.5]
num_iterations = [8000]
is_unbalance = [True, False]

com_id = 0
index = 0
for col in label_cols:
    print(col)
    com_id += 1
    for lr in learning_rate:
        for nl in num_leaves:
            for md in max_depth:
                for bf in bag_frt:
                    for ff in feature_fraction:
                        for l1 in lambda_l1:
                            for l2 in lambda_l2:
                                for ni in num_iterations:
                                    for isb in is_unbalance:
                                        df_lgb.loc[index, 'is_unbalance'] = str(isb)
                                        df_lgb.loc[index, 'num_iterations'] = ni
                                        df_lgb.loc[index, 'lambda_l2'] = l2
                                        df_lgb.loc[index, 'lambda_l1'] = l1
                                        df_lgb.loc[index, 'feature_fraction'] = ff
                                        df_lgb.loc[index, 'bagging_fraction'] = bf
                                        df_lgb.loc[index, 'max_depth'] = md
                                        df_lgb.loc[index, 'num_leaves'] = nl
                                        df_lgb.loc[index, 'learning_rate'] = lr
                                        df_lgb.loc[index, 'label'] = col
                                        df_lgb.loc[index, 'roc'] = 0
                                        df_lgb.loc[index, 'tp'] = 0
                                        df_lgb.loc[index, 'fp'] = 0
                                        df_lgb.loc[index, 'precision'] = 0
                                        df_lgb.loc[index, 'trained'] = 'N'
                                        df_lgb.loc[index, 'combination_id'] = com_id
                                        index += 1
df_lgb.to_csv(PATH + 'lgb_all_gridsearch.csv', index=False)                        

toxic
severe_toxic
obscene
threat
insult
identity_hate


In [ ]:
df_lgb = pd.read_csv(PATH + 'lgb_all_gridsearch.csv')

In [69]:
# df_lgb

In [75]:
base_params = {
    'task': 'train',
    'boosting_type': 'gbdt',
    'objective': 'binary',
    'metric': {'binary', 'auc'},
    'verbosity': 20,
    'verbose': 20,
    'metric': 'auc',
    'bagging_freq': 1,
    'num_threads': 8,
    'early_stopping_round':20,
    'verbose_eval':10
    } 
def get_parameters(df_lgb , col, addition = None):
    params_list =['bagging_fraction',  
                     'feature_fraction', 
                     'lambda_l1', 
                     'lambda_l2', 
                     'learning_rate', 
                     'max_depth',
                     'num_iterations', 
                     'num_leaves',
                     'is_unbalance']
    condition = (df_lgb['trained'] == 'N') & (df_lgb['label'] == col)
    if addition is not None:
        for i in range(len(addition)):
            condition = condition &  (df_lgb[addition[i]['key']] == addition[i]['value'])
#     df = df_lgb[(df_lgb['trained'] == 'N') & (df_lgb['label'] == col)]
    df = df_lgb[condition]
    index = df.index.values
    np.random.shuffle(index)
    next_index = index[0]
    params = dict(df_lgb.loc[next_index, params_list])
    ##### data type fix:
    params['num_leaves'] = int(round(params['num_leaves']))
    params['max_depth'] = int(round(params['max_depth']))
    params['num_iterations'] = int(round(params['num_iterations']))
    params['is_unbalance'] = bool(params['is_unbalance'])
    return params, next_index
    
    
    

In [ ]:
################# random search start
from sklearn.metrics import roc_auc_score, confusion_matrix

%env JOBLIB_TEMP_FOLDER=/tmp
start = 0
for i in range(10000):
    for col in label_cols:
        start += 1
        # create dataset for lightgbm
        params =  base_params.copy()  
        add = [{'key':'num_iterations', 'value': 1200}]
        add = None
        params_get, index_get = get_parameters(df_lgb, col, addition=add)
        params.update(params_get)
        print(start)
        print(col)
        print(index_get)
        print(params)
        ############################################
        gbm_model = lgb.LGBMClassifier(**params)
        gbm_model.fit(train_set[col], y_train_df[col].values, eval_set=[(val_set[col], y_val_df[col].values)], eval_metric =['logloss', 'auc'])
        pred_prob =  gbm_model.predict_proba(val_set[col])[:,1]
        pred = gbm_model.predict(val_set[col])
        roc = roc_auc_score(y_val_df[col].values,pred_prob)
        tn, fp, fn, tp = confusion_matrix(y_val_df[col].values, pred).ravel()
        precision = tp / (tp + fp)
        tpr = tp / (tp + fn)
        fpr = fp / (fp + tn)

        df_lgb.loc[index_get, 'precision'] = precision
        df_lgb.loc[index_get, 'tp'] = tpr
        df_lgb.loc[index_get, 'fp'] = fpr
        df_lgb.loc[index_get, 'roc'] = roc
        df_lgb.loc[index_get, 'trained'] = 'Y'
        df_lgb.loc[index_get, 'roc'] = roc
        print('ROC score is {}'.format(roc) )
        df_lgb.to_csv(PATH + 'lgb_all_gridsearch.csv', index=False) 
        print('done')
        print('===================================')
        
        ################################################
#         lgb_train_set = lgb.Dataset(train_set[col], y_train_df[col].values)
#         lgb_eval_set = lgb.Dataset(val_set[col], y_val_df[col].values, reference=lgb_train_set)


#         gbm_model = lgb.train(params,
#                             lgb_train_set,
#                             valid_sets=lgb_eval_set,
#                            verbose_eval=20)
#         pred_prob =  gbm_model.predict(val_set[col])
#         roc = roc_auc_score(y_val_df[col].values,pred_prob)
#         df_lgb.loc[index_get, 'trained'] = 'Y'
#         df_lgb.loc[index_get, 'roc'] = roc
#         print('ROC score is {}'.format(roc) )
#         df_lgb.to_csv(PATH + 'lgb_all_gridsearch.csv', index=False) 
#         print('done')
#         print('===================================')
    

env: JOBLIB_TEMP_FOLDER=/tmp
1
toxic
470
{'task': 'train', 'boosting_type': 'gbdt', 'objective': 'binary', 'metric': 'auc', 'verbosity': 20, 'verbose': 20, 'bagging_freq': 1, 'num_threads': 8, 'early_stopping_round': 20, 'verbose_eval': 10, 'bagging_fraction': 0.69999999999999996, 'feature_fraction': 0.59999999999999998, 'lambda_l1': 1.0, 'lambda_l2': 0.0, 'learning_rate': 0.20000000000000001, 'max_depth': 5, 'num_iterations': 8000, 'num_leaves': 11, 'is_unbalance': True}


/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:99: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))
/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:104: UserWarning: Found `early_stopping_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[1]	valid_0's auc: 0.828341
Training until validation scores don't improve for 20 rounds.
[2]	valid_0's auc: 0.859613
[3]	valid_0's auc: 0.869397
[4]	valid_0's auc: 0.877937
[5]	valid_0's auc: 0.883386
[6]	valid_0's auc: 0.889539
[7]	valid_0's auc: 0.895379
[8]	valid_0's auc: 0.898444
[9]	valid_0's auc: 0.903317
[10]	valid_0's auc: 0.906247
[11]	valid_0's auc: 0.908609
[12]	valid_0's auc: 0.910792
[13]	valid_0's auc: 0.913523
[14]	valid_0's auc: 0.917272
[15]	valid_0's auc: 0.919694
[16]	valid_0's auc: 0.921029
[17]	valid_0's auc: 0.923092
[18]	valid_0's auc: 0.924596
[19]	valid_0's auc: 0.926147
[20]	valid_0's auc: 0.927652
[21]	valid_0's auc: 0.92896
[22]	valid_0's auc: 0.930726
[23]	valid_0's auc: 0.931965
[24]	valid_0's auc: 0.933511
[25]	valid_0's auc: 0.934813
[26]	valid_0's auc: 0.93634
[27]	valid_0's auc: 0.93707
[28]	valid_0's auc: 0.938679
[29]	valid_0's auc: 0.939804
[30]	valid_0's auc: 0.940475
[31]	valid_0's auc: 0.941506
[32]	valid_0's auc: 0.942151
[33]	valid_0's auc: 0.

[277]	valid_0's auc: 0.971155
[278]	valid_0's auc: 0.971146
[279]	valid_0's auc: 0.971138
[280]	valid_0's auc: 0.971152
[281]	valid_0's auc: 0.971172
[282]	valid_0's auc: 0.97119
[283]	valid_0's auc: 0.971199
[284]	valid_0's auc: 0.971247
[285]	valid_0's auc: 0.971298
[286]	valid_0's auc: 0.971323
[287]	valid_0's auc: 0.971159
[288]	valid_0's auc: 0.971202
[289]	valid_0's auc: 0.971211
[290]	valid_0's auc: 0.971194
[291]	valid_0's auc: 0.971218
[292]	valid_0's auc: 0.971304
[293]	valid_0's auc: 0.97135
[294]	valid_0's auc: 0.971361
[295]	valid_0's auc: 0.971375
[296]	valid_0's auc: 0.971432
[297]	valid_0's auc: 0.971445
[298]	valid_0's auc: 0.971472
[299]	valid_0's auc: 0.971456
[300]	valid_0's auc: 0.971481
[301]	valid_0's auc: 0.971485
[302]	valid_0's auc: 0.971561
[303]	valid_0's auc: 0.971551
[304]	valid_0's auc: 0.971557
[305]	valid_0's auc: 0.971565
[306]	valid_0's auc: 0.971608
[307]	valid_0's auc: 0.971645
[308]	valid_0's auc: 0.971679
[309]	valid_0's auc: 0.971738
[310]	valid_

/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:99: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))
/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:104: UserWarning: Found `early_stopping_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


...

[1]	valid_0's auc: 0.886075
Training until validation scores don't improve for 20 rounds.
[2]	valid_0's auc: 0.922056
[3]	valid_0's auc: 0.92284
[4]	valid_0's auc: 0.934684
[5]	valid_0's auc: 0.935588
[6]	valid_0's auc: 0.937206
[7]	valid_0's auc: 0.94017
[8]	valid_0's auc: 0.94127
[9]	valid_0's auc: 0.946332
[10]	valid_0's auc: 0.947725
[11]	valid_0's auc: 0.94782
[12]	valid_0's auc: 0.948775
[13]	valid_0's auc: 0.949296
[14]	valid_0's auc: 0.949247
[15]	valid_0's auc: 0.949028
[16]	valid_0's auc: 0.949982
[17]	valid_0's auc: 0.950595
[18]	valid_0's auc: 0.95287
[19]	valid_0's auc: 0.954295
[20]	valid_0's auc: 0.955211
[21]	valid_0's auc: 0.956014
[22]	valid_0's auc: 0.956313
[23]	valid_0's auc: 0.957098
[24]	valid_0's auc: 0.957621
[25]	valid_0's auc: 0.958677
[26]	valid_0's auc: 0.9592
[27]	valid_0's auc: 0.959346
[28]	valid_0's auc: 0.959461
[29]	valid_0's auc: 0.959896
[30]	valid_0's auc: 0.960572
[31]	valid_0's auc: 0.961334
[32]	valid_0's auc: 0.962278
[33]	valid_0's auc: 0.9622

[277]	valid_0's auc: 0.986531
[278]	valid_0's auc: 0.986486
[279]	valid_0's auc: 0.986525
[280]	valid_0's auc: 0.986532
[281]	valid_0's auc: 0.986567
[282]	valid_0's auc: 0.986565
[283]	valid_0's auc: 0.986594
[284]	valid_0's auc: 0.986594
[285]	valid_0's auc: 0.986591
[286]	valid_0's auc: 0.986613
[287]	valid_0's auc: 0.986645
[288]	valid_0's auc: 0.98667
[289]	valid_0's auc: 0.986695
[290]	valid_0's auc: 0.986695
[291]	valid_0's auc: 0.9867
[292]	valid_0's auc: 0.986719
[293]	valid_0's auc: 0.986729
[294]	valid_0's auc: 0.986765
[295]	valid_0's auc: 0.986772
[296]	valid_0's auc: 0.986769
[297]	valid_0's auc: 0.986793
[298]	valid_0's auc: 0.986801
[299]	valid_0's auc: 0.986815
[300]	valid_0's auc: 0.986825
[301]	valid_0's auc: 0.986837
[302]	valid_0's auc: 0.986853
[303]	valid_0's auc: 0.986869
[304]	valid_0's auc: 0.9869
[305]	valid_0's auc: 0.986927
[306]	valid_0's auc: 0.986947
[307]	valid_0's auc: 0.986964
[308]	valid_0's auc: 0.986977
[309]	valid_0's auc: 0.986979
[310]	valid_0's

[552]	valid_0's auc: 0.989227
[553]	valid_0's auc: 0.98922
[554]	valid_0's auc: 0.989219
[555]	valid_0's auc: 0.989227
[556]	valid_0's auc: 0.989228
[557]	valid_0's auc: 0.989219
[558]	valid_0's auc: 0.98923
[559]	valid_0's auc: 0.98923
[560]	valid_0's auc: 0.989244
[561]	valid_0's auc: 0.989258
[562]	valid_0's auc: 0.989268
[563]	valid_0's auc: 0.989272
[564]	valid_0's auc: 0.989273
[565]	valid_0's auc: 0.98928
[566]	valid_0's auc: 0.989289
[567]	valid_0's auc: 0.989296
[568]	valid_0's auc: 0.989298
[569]	valid_0's auc: 0.989299
[570]	valid_0's auc: 0.989295
[571]	valid_0's auc: 0.989274
[572]	valid_0's auc: 0.989289
[573]	valid_0's auc: 0.989304
[574]	valid_0's auc: 0.98931
[575]	valid_0's auc: 0.989333
[576]	valid_0's auc: 0.989327
[577]	valid_0's auc: 0.989325
[578]	valid_0's auc: 0.989338
[579]	valid_0's auc: 0.989335
[580]	valid_0's auc: 0.989348
[581]	valid_0's auc: 0.989349
[582]	valid_0's auc: 0.989343
[583]	valid_0's auc: 0.989346
[584]	valid_0's auc: 0.989358
[585]	valid_0's

/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:99: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))
/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:104: UserWarning: Found `early_stopping_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[1]	valid_0's auc: 0.872265
Training until validation scores don't improve for 20 rounds.
[2]	valid_0's auc: 0.879983
[3]	valid_0's auc: 0.918715
[4]	valid_0's auc: 0.921524
[5]	valid_0's auc: 0.933386
[6]	valid_0's auc: 0.941681
[7]	valid_0's auc: 0.952597
[8]	valid_0's auc: 0.959656
[9]	valid_0's auc: 0.963138
[10]	valid_0's auc: 0.965258
[11]	valid_0's auc: 0.964535
[12]	valid_0's auc: 0.966289
[13]	valid_0's auc: 0.966502
[14]	valid_0's auc: 0.967171
[15]	valid_0's auc: 0.968191
[16]	valid_0's auc: 0.971361
[17]	valid_0's auc: 0.970611
[18]	valid_0's auc: 0.97039
[19]	valid_0's auc: 0.971828
[20]	valid_0's auc: 0.971841
[21]	valid_0's auc: 0.972036
[22]	valid_0's auc: 0.973047
[23]	valid_0's auc: 0.972821
[24]	valid_0's auc: 0.973651
[25]	valid_0's auc: 0.974142
[26]	valid_0's auc: 0.974306
[27]	valid_0's auc: 0.974362
[28]	valid_0's auc: 0.97451
[29]	valid_0's auc: 0.974898
[30]	valid_0's auc: 0.974401
[31]	valid_0's auc: 0.974634
[32]	valid_0's auc: 0.975929
[33]	valid_0's auc: 0

In [ ]:
df_lgb.to_csv(PATH + 'lgb_all_gridsearch.csv', index=False) 
print('done')

In [ ]:
##############################
lgb_train_set = {}
lgb_eval_set = {}
gbm_model = {}
y_pred = pd.DataFrame()
y_pred['id'] = test['id']
for col in label_cols:
    # create dataset for lightgbm


    params = {
    'learning_rate': 0.2,
    'task': 'train',
    'boosting_type': 'gbdt',
    'objective': 'binary',
    'metric': {'binary', 'auc'},
    'num_leaves': 31,
    'verbosity': -1,
    'metric': 'auc',
    'data_random_seed': 2,
    'bagging_fraction': 0.8,
    'feature_fraction': 0.6,
    'bagging_freq': 1,
    'nthread': 12,
    'lambda_l1': 1,
    'lambda_l2': 1,
    'early_stopping_round':10
    } 

    print(col)
    lgb_train_set[col] = lgb.Dataset(train_set[col], y_train_df[col].values)
    lgb_eval_set[col] = lgb.Dataset(train_set[col], y_train_df[col].values, reference=lgb_train_set[col])
    

    gbm_model[col] = lgb.train(params,
                        lgb_train_set[col],
                        valid_sets=lgb_eval_set[col],
                       verbose_eval=20)
    y_pred[col] =  gbm_model[col].predict(test_set[col])

In [ ]:
y_pred.to_csv(PATH + 'lgbm_nb_tfidf.csv', index=False)

In [64]:
# lgb_train_set = lgb.Dataset(train_set[col], y_train_df[col].values)
# lgb_eval_set = lgb.Dataset(val_set[col], y_val_df[col].values, reference=lgb_train_set)
aa = lgb.LGBMClassifier(**params)

aa.fit(train_set[col], y_train_df[col].values, eval_set=[(val_set[col], y_val_df[col].values)], eval_metric =['logloss', 'auc'])

/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:99: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))
/home/kai/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:104: UserWarning: Found `early_stopping_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[1]	valid_0's auc: 0.751219
Training until validation scores don't improve for 20 rounds.
[2]	valid_0's auc: 0.770521
[3]	valid_0's auc: 0.680815
[4]	valid_0's auc: 0.631087
[5]	valid_0's auc: 0.634605
[6]	valid_0's auc: 0.637971
[7]	valid_0's auc: 0.686322
[8]	valid_0's auc: 0.693454
[9]	valid_0's auc: 0.693127
[10]	valid_0's auc: 0.679476
[11]	valid_0's auc: 0.679361
[12]	valid_0's auc: 0.68097
[13]	valid_0's auc: 0.680694
[14]	valid_0's auc: 0.678356
[15]	valid_0's auc: 0.680594
[16]	valid_0's auc: 0.679132
[17]	valid_0's auc: 0.678977
[18]	valid_0's auc: 0.677314
[19]	valid_0's auc: 0.682058
[20]	valid_0's auc: 0.667991
[21]	valid_0's auc: 0.670238
[22]	valid_0's auc: 0.669781
Early stopping, best iteration is:
[2]	valid_0's auc: 0.770521


LGBMClassifier(bagging_fraction=0.69999999999999996, bagging_freq=1,
        boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
        early_stopping_round=20, feature_fraction=0.59999999999999998,
        is_unbalance=True, lambda_l1=1.0, lambda_l2=1.0, learning_rate=3,
        max_depth=3, metric='auc', min_child_samples=20,
        min_child_weight=0.001, min_split_gain=0.0, n_estimators=100,
        n_jobs=-1, num_iterations=8000, num_leaves=61, num_threads=8,
        objective='binary', random_state=None, reg_alpha=0.0,
        reg_lambda=0.0, silent=True, subsample=1.0,
        subsample_for_bin=200000, subsample_freq=1, task='train',
        verbose=20, verbose_eval=10, verbosity=20)

In [65]:
aa.predict(val_set[col])

array([1, 1, 1, ..., 1, 1, 1])

In [61]:
params['learning_rate'] = 3